# Query Processor

#### Queries are randomly generated from queries_generator.py and saved in ./static/auxiliary_files/queries.csv

In [1]:
import os
import pandas as pd
from utilityMethods import SORT_BY, __get_path_points, ROUTE_FROM
import time
from Path import Path
import ast

policy = [SORT_BY.Time, SORT_BY.Distance, SORT_BY.Risk, SORT_BY.POIScore]

# Precomputed from queries_generator.py
queries_file = 'static/auxiliary_files/queries.csv'
queries = pd.read_csv(queries_file)

### Get distance, duration and routes from each query

In [2]:
import time

queries_result_array = []

print("total number of indices: "+str(len(queries)))
print("total number of indices: "+str(len(queries)))
dist = []
dur = []
routes = []
failed_indices = [] # record the failed attempets

for index, query in queries.iterrows():
    print(index)
    q = query['query']
    try:
        r, dist_tags, duration_tags = __get_path_points(q, ROUTE_FROM.OSRM, num_of_routes=5)
        
        dist.append(dist_tags)
        dur.append(duration_tags)
        routes.append(r)
    
    # Wait 5 and try again
    except Exception as e:
        time.sleep(5)
        try:
            r, dist_tags, duration_tags = __get_path_points(q, ROUTE_FROM.OSRM, num_of_routes=5)
            
            dist.append(dist_tags)
            dur.append(duration_tags)
            routes.append(r)
        except Exception as ee:
            failed_indices.append(index)
            print("\t==>> FAILED")
        
    


total number of indices: 1924
total number of indices: 1924
0
1
2
3
4
5


KeyboardInterrupt: 

In [3]:
print(len(dur))
print(len(dist))
print(len(routes))
print(len(queries))

if len(failed_indices) > 0:
    queries = queries.drop(failed_indices)
    
queries['duration'] = dur
queries['dist'] = dist
queries['routes'] = routes

1924
1924
1924
1924


In [4]:
queries.head(10)

source              destination  \
0          [43.669871, -79.280689]  [43.672366, -79.384658]   
1          [43.669871, -79.280689]  [43.672958, -79.319656]   
2          [43.669871, -79.280689]   [43.67078, -79.295951]   
3          [43.669871, -79.280689]   [43.670128, -79.39431]   
4          [43.669871, -79.280689]   [43.67158, -79.293543]   
5          [43.669871, -79.280689]  [43.671022, -79.386054]   
6          [43.669871, -79.280689]  [43.671364, -79.412833]   
7          [43.669871, -79.280689]  [43.671713, -79.393146]   
8          [43.669871, -79.280689]  [43.670004, -79.385741]   
9  [43.669871, -79.38346166666666]  [43.672366, -79.384658]   

                                       category  \
0  Office Supplies, Stationery, and Gift Stores   
1  Office Supplies, Stationery, and Gift Stores   
2  Office Supplies, Stationery, and Gift Stores   
3  Office Supplies, Stationery, and Gift Stores   
4  Office Supplies, Stationery, and Gift Stores   
5  Office Supplies, Stationery, and Gift Stores   
6  Office Supplies, Stationery, and Gift Stores   
7  Office Supplies, Stationery, and Gift Stores   
8  Office Supplies, Stationery, and Gift Stores   
9  Office Supplies, Stationery, and Gift Stores   

                                               query              duration  \
0  http://router.project-osrm.org/route/v1/car/-7...      [18.69667, 18.9]   
1  http://router.project-osrm.org/route/v1/car/-7...        [7.72667, 8.0]   
2  http://router.project-osrm.org/route/v1/foot/-...             [2.89667]   
3  http://router.project-osrm.org/route/v1/car/-7...     [19.71667, 20.07]   
4  http://router.project-osrm.org/route/v1/car/-7...             [2.43333]   
5  http://router.project-osrm.org/route/v1/foot/-...     [19.21, 19.45833]   
6  http://router.project-osrm.org/route/v1/car/-7...  [22.47167, 24.29667]   
7  http://router.project-osrm.org/route/v1/car/-7...    [20.03833, 20.515]   
8  http://router.project-osrm.org/route/v1/car/-7...    [18.795, 18.96667]   
9  http://router.project-osrm.org/route/v1/foot/-...             [1.00333]   

                 dist                                             routes  
0  [10.6921, 11.1126]  [[[43.671032, -79.282504], [43.671257, -79.282...  
1       [4.7004, 4.0]  [[[43.671032, -79.282504], [43.671257, -79.282...  
2            [1.3316]  [[[43.671032, -79.282504], [43.671257, -79.282...  
3  [12.5038, 11.8988]  [[[43.671032, -79.282504], [43.671257, -79.282...  
4            [1.1208]  [[[43.671032, -79.282504], [43.671257, -79.282...  
5  [10.8544, 11.9673]  [[[43.671032, -79.282504], [43.671257, -79.282...  
6  [14.7636, 13.8282]  [[[43.671032, -79.282504], [43.671257, -79.282...  
7  [12.5045, 11.8994]  [[[43.671032, -79.282504], [43.671257, -79.282...  
8  [10.6863, 11.0412]  [[[43.671032, -79.282504], [43.671257, -79.282...  
9            [0.4218]  [[[43.669865, -79.383491], [43.669958, -79.383...

In [5]:
# Check point to not lose data in case of a crash
output_results_to = 'static/auxiliary_files/computed_queries2.csv'

if os.path.isfile(output_results_to):
    os.remove(output_results_to)
    
queries.to_csv(output_results_to, index=False)

In [6]:
print("length of duration : "+str(len(dur)))
print("length of distance : "+str(len(dist)))
print("length of routes : "+str(len(routes)))

length of duration : 1924
length of distance : 1924
length of routes : 1924


# Calculate Risk of paths

In [2]:
def get_trip_if_exists(source, destination, query):
    df_trip_path = 'df_trips.csv'
    df_trip = pd.read_csv(df_trip_path)

    distances = ast.literal_eval(query['dist'])
    durations = ast.literal_eval(query['duration'])
    path_list = ast.literal_eval(query['routes'])
    
    paths_hexagons, paths_discretized_points, paths_discretized_linestrings = [], [], []
    isFound = False

    # Path exists
    if os.path.exists(df_trip_path):
        
        # Doesn't include mode of transit as there is no distinction in OSRM
        row = df_trip[(df_trip['source'] == str(source)) &
                      (df_trip['destination'] == str(destination))]

        # Take into account a reverse trip with the assumption that the distance and
        # duration remains the same
        if len(row) == 0:
            row = df_trip[(df_trip['source'] == str(destination)) &
                          (df_trip['destination'] == str(source))]
                
        # Entry exists! retrive and use it
        if len(row) > 0:
            print("\t\t\tTrip Exists!")
            paths_discretized_points = ast.literal_eval(row['discretized_points'].values[0])

            isFound = True
    
    total_risks = []
    
    for i in range(len(path_list)):
        if not isFound:
            new_path = Path(i, path_list[i], distances[i], durations[i], ROUTE_FROM=ROUTE_FROM.OSRM, hexagons=None,
                            discretized_points=None)
        else:
            new_path = Path(i, coordinates=path_list[i], distance=distances[i], time=durations[i],
                            ROUTE_FROM=ROUTE_FROM.OSRM, 
                            discretized_points=paths_discretized_points[i])
      
        new_path.set_risk_of_path()

        new_path_risks = new_path.get_risk_of_path_over_a_week() 
        total_risks.append(new_path_risks)

        # add the path to the list of current paths
        paths_discretized_points.append(new_path.discretized_points)
        paths_hexagons.append(new_path.get_hexagons())

    if not isFound:
        row = pd.DataFrame({'source': [query['source']], 'destination': [query['destination']], 'distance': [distances],
                            'duration': [durations], 'routes': [path_list], 'hexagons': [paths_hexagons],
                            'discretized_points': [paths_discretized_points]})

        row.to_csv(df_trip_path, mode='a', index=False, header=False)
        
    return total_risks

In [3]:
# Precomputed from above
queries_file = 'static/auxiliary_files/computed_queries2.csv'
queries = pd.read_csv(queries_file)

len(queries)

1924

In [4]:
GDF_FILE = 'hex_gdf.csv'
path_risks = []
i = 0
main_start = time.time()
for index, query in queries.iterrows():
#     if index >= 197:
    start = time.time()
    # set and retrieve risk of path
    total_risks = []
    print(index)

    if 'car' in query['query']:
        # 0 risk if its a car
        total_risks = [0]*len(ast.literal_eval(query['routes']))

    else:
        total_risks = get_trip_if_exists(query['source'], query['destination'], query)

    path_risks.append(total_risks)
    end = time.time()
    print(str(i) + ".\t finished, " + "time took to process request: " + str(round((end - start) / 60, 2)) + " min")
#     print("\tpath_risks = "+str(total_risks))
    i += 1

main_end = time.time()
print("finished, " + "time took to process request: " + str(round((main_end - main_start) / 60, 2)) + " min")


0
0.	 finished, time took to process request: 0.0 min
1
1.	 finished, time took to process request: 0.0 min
2
			Trip Exists!
2.	 finished, time took to process request: 0.04 min
3
3.	 finished, time took to process request: 0.0 min
4
4.	 finished, time took to process request: 0.0 min
5
			Trip Exists!
5.	 finished, time took to process request: 0.16 min
6
6.	 finished, time took to process request: 0.0 min
7
7.	 finished, time took to process request: 0.0 min
8
8.	 finished, time took to process request: 0.0 min
9
			Trip Exists!
9.	 finished, time took to process request: 0.03 min
10
			Trip Exists!
10.	 finished, time took to process request: 0.08 min
11
11.	 finished, time took to process request: 0.0 min
12
12.	 finished, time took to process request: 0.0 min
13
13.	 finished, time took to process request: 0.0 min
14
14.	 finished, time took to process request: 0.0 min
15
			Trip Exists!
15.	 finished, time took to process request: 0.16 min
16
			Trip Exists!
16.	 finished, time 

129.	 finished, time took to process request: 0.16 min
130
			Trip Exists!
130.	 finished, time took to process request: 0.17 min
131
			Trip Exists!
131.	 finished, time took to process request: 0.2 min
132
			Trip Exists!
132.	 finished, time took to process request: 0.18 min
133
133.	 finished, time took to process request: 0.0 min
134
134.	 finished, time took to process request: 0.0 min
135
135.	 finished, time took to process request: 0.0 min
136
136.	 finished, time took to process request: 0.0 min
137
137.	 finished, time took to process request: 0.0 min
138
138.	 finished, time took to process request: 0.0 min
139
139.	 finished, time took to process request: 0.0 min
140
			Trip Exists!
140.	 finished, time took to process request: 0.17 min
141
			Trip Exists!
141.	 finished, time took to process request: 0.16 min
142
142.	 finished, time took to process request: 0.0 min
143
			Trip Exists!
143.	 finished, time took to process request: 0.2 min
144
			Trip Exists!
144.	 finishe

252.	 finished, time took to process request: 0.16 min
253
			Trip Exists!
253.	 finished, time took to process request: 0.16 min
254
			Trip Exists!
254.	 finished, time took to process request: 0.04 min
255
255.	 finished, time took to process request: 0.0 min
256
			Trip Exists!
256.	 finished, time took to process request: 0.23 min
257
257.	 finished, time took to process request: 0.0 min
258
			Trip Exists!
258.	 finished, time took to process request: 0.1 min
259
259.	 finished, time took to process request: 0.0 min
260
260.	 finished, time took to process request: 0.0 min
261
			Trip Exists!
261.	 finished, time took to process request: 0.04 min
262
262.	 finished, time took to process request: 0.0 min
263
263.	 finished, time took to process request: 0.0 min
264
			Trip Exists!
264.	 finished, time took to process request: 0.15 min
265
			Trip Exists!
265.	 finished, time took to process request: 0.07 min
266
			Trip Exists!
266.	 finished, time took to process request: 0.09 mi

377.	 finished, time took to process request: 0.07 min
378
378.	 finished, time took to process request: 0.0 min
379
			Trip Exists!
379.	 finished, time took to process request: 0.06 min
380
380.	 finished, time took to process request: 0.0 min
381
			Trip Exists!
381.	 finished, time took to process request: 0.09 min
382
382.	 finished, time took to process request: 0.0 min
383
			Trip Exists!
383.	 finished, time took to process request: 0.11 min
384
			Trip Exists!
384.	 finished, time took to process request: 0.03 min
385
385.	 finished, time took to process request: 0.0 min
386
			Trip Exists!
386.	 finished, time took to process request: 0.12 min
387
			Trip Exists!
387.	 finished, time took to process request: 0.13 min
388
388.	 finished, time took to process request: 0.0 min
389
389.	 finished, time took to process request: 0.0 min
390
			Trip Exists!
390.	 finished, time took to process request: 0.13 min
391
391.	 finished, time took to process request: 0.0 min
392
392.	 fini

501.	 finished, time took to process request: 0.07 min
502
502.	 finished, time took to process request: 0.0 min
503
			Trip Exists!
503.	 finished, time took to process request: 0.06 min
504
			Trip Exists!
504.	 finished, time took to process request: 0.07 min
505
505.	 finished, time took to process request: 0.0 min
506
506.	 finished, time took to process request: 0.0 min
507
			Trip Exists!
507.	 finished, time took to process request: 0.1 min
508
			Trip Exists!
508.	 finished, time took to process request: 0.04 min
509
509.	 finished, time took to process request: 0.0 min
510
			Trip Exists!
510.	 finished, time took to process request: 0.05 min
511
			Trip Exists!
511.	 finished, time took to process request: 0.08 min
512
512.	 finished, time took to process request: 0.0 min
513
			Trip Exists!
513.	 finished, time took to process request: 0.23 min
514
514.	 finished, time took to process request: 0.0 min
515
			Trip Exists!
515.	 finished, time took to process request: 0.04 mi

...

1363.	 finished, time took to process request: 0.17 min
1364
			Trip Exists!
1364.	 finished, time took to process request: 0.15 min
1365
			Trip Exists!
1365.	 finished, time took to process request: 0.23 min
1366
1366.	 finished, time took to process request: 0.0 min
1367
1367.	 finished, time took to process request: 0.0 min
1368
1368.	 finished, time took to process request: 0.0 min
1369
			Trip Exists!
1369.	 finished, time took to process request: 0.07 min
1370
			Trip Exists!
1370.	 finished, time took to process request: 0.2 min
1371
			Trip Exists!
1371.	 finished, time took to process request: 0.21 min
1372
1372.	 finished, time took to process request: 0.0 min
1373
1373.	 finished, time took to process request: 0.0 min
1374
			Trip Exists!
1374.	 finished, time took to process request: 0.14 min
1375
1375.	 finished, time took to process request: 0.0 min
1376
			Trip Exists!
1376.	 finished, time took to process request: 0.14 min
1377
1377.	 finished, time took to process req

1485.	 finished, time took to process request: 0.12 min
1486
1486.	 finished, time took to process request: 0.0 min
1487
			Trip Exists!
1487.	 finished, time took to process request: 0.12 min
1488
1488.	 finished, time took to process request: 0.0 min
1489
1489.	 finished, time took to process request: 0.0 min
1490
1490.	 finished, time took to process request: 0.0 min
1491
1491.	 finished, time took to process request: 0.0 min
1492
1492.	 finished, time took to process request: 0.0 min
1493
			Trip Exists!
1493.	 finished, time took to process request: 0.04 min
1494
			Trip Exists!
1494.	 finished, time took to process request: 0.16 min
1495
1495.	 finished, time took to process request: 0.0 min
1496
1496.	 finished, time took to process request: 0.0 min
1497
			Trip Exists!
1497.	 finished, time took to process request: 0.11 min
1498
1498.	 finished, time took to process request: 0.0 min
1499
1499.	 finished, time took to process request: 0.0 min
1500
			Trip Exists!
1500.	 finished

1605.	 finished, time took to process request: 0.17 min
1606
1606.	 finished, time took to process request: 0.0 min
1607
1607.	 finished, time took to process request: 0.0 min
1608
1608.	 finished, time took to process request: 0.0 min
1609
1609.	 finished, time took to process request: 0.0 min
1610
1610.	 finished, time took to process request: 0.0 min
1611
1611.	 finished, time took to process request: 0.0 min
1612
1612.	 finished, time took to process request: 0.0 min
1613
			Trip Exists!
1613.	 finished, time took to process request: 0.07 min
1614
1614.	 finished, time took to process request: 0.0 min
1615
			Trip Exists!
1615.	 finished, time took to process request: 0.18 min
1616
1616.	 finished, time took to process request: 0.0 min
1617
			Trip Exists!
1617.	 finished, time took to process request: 0.04 min
1618
1618.	 finished, time took to process request: 0.0 min
1619
1619.	 finished, time took to process request: 0.0 min
1620
1620.	 finished, time took to process request: 0

1726.	 finished, time took to process request: 0.2 min
1727
			Trip Exists!
1727.	 finished, time took to process request: 0.1 min
1728
			Trip Exists!
1728.	 finished, time took to process request: 0.11 min
1729
1729.	 finished, time took to process request: 0.0 min
1730
1730.	 finished, time took to process request: 0.0 min
1731
1731.	 finished, time took to process request: 0.0 min
1732
1732.	 finished, time took to process request: 0.0 min
1733
			Trip Exists!
1733.	 finished, time took to process request: 0.13 min
1734
1734.	 finished, time took to process request: 0.0 min
1735
1735.	 finished, time took to process request: 0.0 min
1736
			Trip Exists!
1736.	 finished, time took to process request: 0.14 min
1737
			Trip Exists!
1737.	 finished, time took to process request: 0.14 min
1738
1738.	 finished, time took to process request: 0.0 min
1739
			Trip Exists!
1739.	 finished, time took to process request: 0.1 min
1740
1740.	 finished, time took to process request: 0.0 min
1741


1846.	 finished, time took to process request: 0.05 min
1847
1847.	 finished, time took to process request: 0.0 min
1848
			Trip Exists!
1848.	 finished, time took to process request: 0.03 min
1849
			Trip Exists!
1849.	 finished, time took to process request: 0.16 min
1850
			Trip Exists!
1850.	 finished, time took to process request: 0.12 min
1851
			Trip Exists!
1851.	 finished, time took to process request: 0.16 min
1852
			Trip Exists!
1852.	 finished, time took to process request: 0.2 min
1853
1853.	 finished, time took to process request: 0.0 min
1854
			Trip Exists!
1854.	 finished, time took to process request: 0.07 min
1855
			Trip Exists!
1855.	 finished, time took to process request: 0.06 min
1856
1856.	 finished, time took to process request: 0.0 min
1857
1857.	 finished, time took to process request: 0.0 min
1858
1858.	 finished, time took to process request: 0.0 min
1859
1859.	 finished, time took to process request: 0.0 min
1860
			Trip Exists!
1860.	 finished, time too

In [5]:
print(len(queries))
print(len(path_risks))

1924
1924


In [6]:
queries['path_risks'] = path_risks
path_risks

[[0, 0],
 [0, 0],
 [[1.665,
   1.64,
   1.8533333333333335,
   2.3133333333333335,
   1.6750000000000003,
   1.5999999999999999,
   1.0383333333333333,
   2.0733333333333333,
   1.9333333333333331,
   2.205,
   1.8583333333333334,
   1.9066666666666667,
   2.5416666666666665,
   2.0383333333333336,
   2.538333333333333,
   1.46,
   2.1266666666666665,
   2.3049999999999997,
   2.235,
   1.3466666666666667,
   1.4183333333333334,
   2.6516666666666664,
   1.5116666666666667,
   1.7533333333333334,
   2.5316666666666667,
   2.1416666666666666,
   1.8283333333333331,
   2.0866666666666664,
   2.3516666666666666,
   2.0183333333333335,
   1.9033333333333333,
   2.1016666666666666,
   1.2033333333333331,
   1.4083333333333334,
   1.7149999999999999,
   2.4783333333333335,
   1.4849999999999999,
   1.8783333333333332,
   2.118333333333333,
   2.1283333333333334,
   1.2766666666666666,
   2.058333333333333,
   2.4283333333333332,
   2.5683333333333334,
   1.7616666666666667,
   1.608333333333

In [11]:
# Check point to not lose data in case of a crash
output_results_to = 'static/auxiliary_files/computed_queries3.csv'

if os.path.isfile(output_results_to):
    os.remove(output_results_to)
    
queries.to_csv(output_results_to, index=False)

### Add poi risks

In [12]:
relevant_queries = pd.read_csv('static/auxiliary_files/computed_queries3.csv')
poi_risks = pd.read_csv('GTA_risks.csv')

relevant_queries['poi_longitude'] = [ast.literal_eval(relevant_queries['destination'][i])[1] for i in range(len(relevant_queries))]
relevant_queries['poi_latitude'] = [ast.literal_eval(relevant_queries['destination'][i])[0] for i in range(len(relevant_queries))]


relevant_queries = relevant_queries.drop(columns=['Unnamed: 0'])
relevant_queries

source              destination  \
0              [43.669871, -79.280689]  [43.672366, -79.384658]   
1              [43.669871, -79.280689]  [43.672958, -79.319656]   
2              [43.669871, -79.280689]   [43.67078, -79.295951]   
3              [43.669871, -79.280689]   [43.670128, -79.39431]   
4              [43.669871, -79.280689]   [43.67158, -79.293543]   
...                                ...                      ...   
1919  [43.77805720000001, -79.5470428]   [43.74055, -79.503603]   
1920  [43.77805720000001, -79.5470428]  [43.770943, -79.540848]   
1921  [43.77805720000001, -79.5470428]  [43.769351, -79.553925]   
1922  [43.77805720000001, -79.5470428]  [43.727751, -79.478053]   
1923  [43.77805720000001, -79.5470428]  [43.725815, -79.402928]   

                                          category  \
0     Office Supplies, Stationery, and Gift Stores   
1     Office Supplies, Stationery, and Gift Stores   
2     Office Supplies, Stationery, and Gift Stores   
3     Office Supplies, Stationery, and Gift Stores   
4     Office Supplies, Stationery, and Gift Stores   
...                                            ...   
1919                       Outpatient Care Centers   
1920                       Outpatient Care Centers   
1921                       Outpatient Care Centers   
1922                       Outpatient Care Centers   
1923                       Outpatient Care Centers   

                                                  query            duration  \
0     http://router.project-osrm.org/route/v1/car/-7...    [18.69667, 18.9]   
1     http://router.project-osrm.org/route/v1/car/-7...      [7.72667, 8.0]   
2     http://router.project-osrm.org/route/v1/foot/-...           [2.89667]   
3     http://router.project-osrm.org/route/v1/car/-7...   [19.71667, 20.07]   
4     http://router.project-osrm.org/route/v1/car/-7...           [2.43333]   
...                                                 ...                 ...   
1919  http://router.project-osrm.org/route/v1/car/-7...          [11.14167]   
1920  http://router.project-osrm.org/route/v1/car/-7...  [2.74333, 3.26667]   
1921  http://router.project-osrm.org/route/v1/car/-7...           [3.35667]   
1922  http://router.project-osrm.org/route/v1/car/-7...  [13.315, 16.28833]   
1923  http://router.project-osrm.org/route/v1/foot/-...          [20.76667]   

                    dist                                             routes  \
0     [10.6921, 11.1126]  [[[43.671032, -79.282504], [43.671257, -79.282...   
1          [4.7004, 4.0]  [[[43.671032, -79.282504], [43.671257, -79.282...   
2               [1.3316]  [[[43.671032, -79.282504], [43.671257, -79.282...   
3     [12.5038, 11.8988]  [[[43.671032, -79.282504], [43.671257, -79.282...   
4               [1.1208]  [[[43.671032, -79.282504], [43.671257, -79.282...   
...                  ...                                                ...   
1919            [7.5108]  [[[43.778079, -79.546914], [43.777713, -79.546...   
1920    [1.2753, 1.3678]  [[[43.778079, -79.546914], [43.777713, -79.546...   
1921            [1.7201]  [[[43.778079, -79.546914], [43.777713, -79.546...   
1922   [12.975, 11.2931]  [[[43.778079, -79.546914], [43.777713, -79.546...   
1923           [20.1471]  [[[43.778079, -79.546914], [43.777713, -79.546...   

                                             path_risks  poi_longitude  \
0                                                [0, 0]     -79.384658   
1                                                [0, 0]     -79.319656   
2     [[1.665, 1.64, 1.8533333333333335, 2.313333333...     -79.295951   
3                                                [0, 0]     -79.394310   
4                                                   [0]     -79.293543   
...                                                 ...            ...   
1919                                                [0]     -79.503603   
1920                                             [0, 0]     -79.540848   
1921          

In [13]:
normal_strings = []
skewed_strings = []
uniform_strings = []

for i in range(168):
    relevant_queries = pd.merge(relevant_queries, poi_risks[['longitude', 
                                              'latitude',
                                              'top_category',
                                              'normal_risks' + str(i), 
                                              'skewed_risks' + str(i), 
                                              'uniform_risks_' + str(i)]], 
                left_on=['poi_longitude','poi_latitude','category'], 
                right_on=['longitude','latitude','top_category']).drop(columns= ['longitude', 'latitude','top_category'])


relevant_queries

source              destination  \
0               [43.669871, -79.280689]  [43.672366, -79.384658]   
1       [43.669871, -79.38346166666666]  [43.672366, -79.384658]   
2       [43.669871, -79.48623433333333]  [43.672366, -79.384658]   
3               [43.672195, -79.280689]  [43.672366, -79.384658]   
4       [43.672195, -79.38346166666666]  [43.672366, -79.384658]   
...                                 ...                      ...   
1919  [43.750375600000005, -79.5470428]  [43.731522, -79.599161]   
1920   [43.76421640000001, -79.4655906]  [43.731522, -79.599161]   
1921   [43.76421640000001, -79.5470428]  [43.731522, -79.599161]   
1922   [43.77805720000001, -79.4655906]  [43.731522, -79.599161]   
1923   [43.77805720000001, -79.5470428]  [43.731522, -79.599161]   

                                          category  \
0     Office Supplies, Stationery, and Gift Stores   
1     Office Supplies, Stationery, and Gift Stores   
2     Office Supplies, Stationery, and Gift Stores   
3     Office Supplies, Stationery, and Gift Stores   
4     Office Supplies, Stationery, and Gift Stores   
...                                            ...   
1919                       Outpatient Care Centers   
1920                       Outpatient Care Centers   
1921                       Outpatient Care Centers   
1922                       Outpatient Care Centers   
1923                       Outpatient Care Centers   

                                                  query              duration  \
0     http://router.project-osrm.org/route/v1/car/-7...      [18.69667, 18.9]   
1     http://router.project-osrm.org/route/v1/foot/-...             [1.00333]   
2     http://router.project-osrm.org/route/v1/car/-7...              [14.115]   
3     http://router.project-osrm.org/route/v1/foot/-...    [18.84333, 18.915]   
4     http://router.project-osrm.org/route/v1/foot/-...             [0.28833]   
...                                                 ...                   ...   
1919  http://router.project-osrm.org/route/v1/car/-7...             [8.49667]   
1920  http://router.project-osrm.org/route/v1/car/-7...     [18.84833, 19.35]   
1921  http://router.project-osrm.org/route/v1/car/-7...  [10.52833, 12.63667]   
1922  http://router.project-osrm.org/route/v1/foot/-...  [21.94167, 23.05333]   
1923  http://router.project-osrm.org/route/v1/car/-7...    [12.445, 12.71833]   

                    dist                                             routes  \
0     [10.6921, 11.1126]  [[[43.671032, -79.282504], [43.671257, -79.282...   
1               [0.4218]  [[[43.669865, -79.383491], [43.669958, -79.383...   
2                [9.888]  [[[43.66987, -79.486239], [43.669859, -79.4862...   
3     [10.7984, 11.1502]  [[[43.672237, -79.280497], [43.67225, -79.2805...   
4               [0.1349]  [[[43.672075, -79.383417], [43.67207, -79.3834...   
...                  ...                                                ...   
1919            [5.5013]  [[[43.75012, -79.547192], [43.750068, -79.5474...   
1920  [12.7409, 18.4065]  [[[43.764186, -79.465865], [43.76545, -79.4661...   
1921    [7.4421, 9.0812]  [[[43.764319, -79.547255], [43.764343, -79.547...   
1922  [13.8363, 18.9354]  [[[43.77812, -79.464717], [43.778591, -79.4647...   
1923   [10.8254, 8.9646]  [[[43.778079, -79.546914], [43.777713, -79.546...   

                                             path_risks  poi_longitude  \
0                                                [0, 0]     -79.384658   
1     [[0.47, 0.45, 0.76, 0.94, 0.77, 0.98, 0.72, 0....     -79.384658   
2                                                   [0]     -79.384658   
3     [[9.718333333333332, 11.058333333333334, 11.24...     -79.384658   
4     [[0.47, 0.45, 0.76, 0.94, 0.77, 0.98, 0.72, 0....     -79.384658   
...                                                 ...            ...   
1919                                                [0]     -79.599161   
1920                                             [0, 

In [15]:
relevant_queries.to_csv(output_results_to, index=False)